## Erreur pour régression linéaire 

On regarde le comportement des erreurs d'entrainement et de généralisation en fonction de la dimension du problème.
La dimension d'entrainement est 100.

In [38]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Wed Jul  6 11:05:24 2022

@author: franck
"""

from ipywidgets import interact, interactive, fixed, interact_manual, interactive_output
import ipywidgets as widgets
import numpy as np
import matplotlib.pyplot as plt
import random as rand
from sklearn import datasets, linear_model
import copy as cp

import numpy.random as randn
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import ElasticNet
from sklearn.pipeline import Pipeline


import copy 


In [39]:
def generate_data(sigma,beta,alpha,n,m): ## génère n exemple dans R^m avec le modèle $f$
    X = np.zeros((n,m)) ## creation de la matrice à n exemple de dimension m
    Y = np.zeros(n) ## creation de la matrice à n exemple de dimension l
    Xhat = np.zeros((n,m)) ## creation de la matrice à n exemple de dimension m
    Yhat = np.zeros(n)
    eps = randn.normal(0.0,sigma,n) ## vecteur des bruits
    meanY = 0.0
    meanX = np.zeros(m)
    varianceX = np.zeros(m)
    for i in range(0, n):
        X[i,:]=randn.uniform(0.0,2.0,m) # m nombre aléatoire entre 0 et 1
        Y[i]= np.dot(beta,X[i,:])+alpha+eps[i]
        meanX[:] = meanX + X[i,:]/n
        meanY = meanY + Y[i]/n 
        varianceX[:] = varianceX[:] + X[i,:]*X[i,:]/n
        
    for i in range(0, n):
        Xhat[i,:]= (X[i,:]-meanX[:])/(varianceX[:])
        Yhat[i]= (Y[i]-meanY)
    
    return X,Y,eps

# calcul les erreur pour la regression Rdige
def errorR(lam,beta_hat,alpha_hat,X,Y,n,m):
    nnew=100
    if lam >0:
        reg = Ridge(alpha=lam,tol=10-8,solver='svd').fit(X,Y)
    else: 
        reg = LinearRegression().fit(X, Y)
     
    Yref = np.zeros(n); Ycom = np.zeros(n)   
    Ynewref = np.zeros(nnew); Ynewcom = np.zeros(nnew)
       
    Xnew = np.zeros((nnew,m)) # entrées et sortiesde l'échantillon de test
    for i in range(0, nnew):
        Xnew[i,:]=randn.uniform(0.0,2.0,m)   
        Ynewref[i]= np.dot(beta_hat,Xnew[i,:])+alpha_hat
        Ynewcom[i] = np.dot(reg.coef_,Xnew[i,:])+reg.intercept_

    for i in range(0, n): # sortie de l'échantillon d'entrainement
        Ycom[i] = np.dot(reg.coef_,X[i,:])+reg.intercept_
        Yref[i]= np.dot(beta_hat,X[i,:])+alpha_hat

    Error=0.0;  ErrorQuad=0.0; normp=0.0

    Error = np.mean((Ynewref - Ynewcom)**2)
    ErrorQuad = np.mean((Y - Ycom)**2) 

    normp = reg.intercept_**2
    for i in range(0,m):
        normp = normp+reg.coef_[i]**2
    normp/(m+1) 
    return Error,ErrorQuad,normp


In [40]:
def plot_overfitting_dim(bruit,dim): ## affiche les erreurs pour une regréssion classique
    n = 100 
    EQ=[]; E=[]; B=[]; V=[]; iterl=[] ## liste de stockage
    for m in range(10,dim,5):
        beta= randn.uniform(-1.0,1.0,m)
        alpha = randn.uniform(-1.0,1.0)
        X,Y,eps= generate_data(bruit,beta,alpha,n,m)
        Error,ErrorQuad,normp = errorR(0.0,beta,alpha,X,Y,n,m)
        E.append(Error); EQ.append(ErrorQuad); iterl.append(m)

    fig, axes = plt.subplots(1, 2, figsize=(18, 5))
    
    axes[0].plot(iterl,E,'o-',alpha=0.8, color='#0571b0',ms=5)
    if dim>100:
        axes[0].axvline(x=100, color='#ca0020')
    axes[0].title.set_text('Erreur généralisation')

    axes[1].plot(iterl,EQ,'o-',alpha=0.8, color='#0571b0',ms=5)
    if dim>100:
        axes[1].axvline(x=100, color='#ca0020')
    axes[1].title.set_text('Erreur entrainement')
   
    plt.show()

In [41]:
bruit = widgets.FloatSlider(value=0.005,min=0.0,max=0.1,step=0.005,description="Bruit")
dim = widgets.IntSlider(value=50,min=20,max=400,step=5,description="Dimension")


ui = widgets.HBox([bruit,dim])

out = widgets.interactive_output(plot_overfitting_dim, {'bruit':bruit,'dim': dim})

In [37]:
display(ui,out)

Output(outputs=({'output_type': 'display_data', 'data': {'text/plain': '<Figure size 1296x360 with 2 Axes>', '…